

---


#Visualização dos dados do MPU6050 e sensores de umidade



#Antes de executar o próximo passo você deve





1.   Baixar o arquivo para analisar em https://drive.google.com/drive/folders/16HTaQ_RybY1WZSA75zdFCa0uHqkdjaMt?usp=sharing
2.   Adiconar o arquivo ao colab, para isso, veja o video https://www.youtube.com/watch?v=PtTEukfwAig&feature=youtu.be
3. Dados de chuva baixados em http://www2.cemaden.gov.br/mapainterativo/#

### Canal dos testes pode ser visto em 
https://thingspeak.com/channels/1670099

In [ ]:
!pip install --upgrade plotly  ## É instalada a mais nova versã do Plotly Para ter gráficos interativos

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
     |████████████████████████████████| 15.3 MB 11.9 MB/s 
  Attempting uninstall: plotly
    Found existing installation: plotly 5.5.0
    Uninstalling plotly-5.5.0:
      Successfully uninstalled plotly-5.5.0


In [ ]:
#Carregar Bibliotecas
import numpy as np
import pandas as pd
import plotly.express as px
import matplotlib.pyplot as plt
import math
# import dash

In [ ]:
#Pedir ao pandas que mostre graficos no plotly
pd.options.plotting.backend = "plotly"

In [ ]:
#É lido o arquivo onde estão os dados
dados=pd.read_csv("20221004_RESULTADOS_TESTE UFF ESTUFA.csv")
dados = dados.drop(dados.columns[[9,10,11,12]], axis=1) #Elimina colunas com informações geograficas do experimento, neste caso não fornecidas pelo thingspeak, pelo que não contem infomração relevante.

In [ ]:
display(dados)

created_at  entry_id  field1  field2  field3  field4  \
0      2022-03-08T16:15:17-03:00         1       0       0       0    3653   
1      2022-03-08T16:15:37-03:00         2      -1      -1      -1    3653   
2      2022-03-08T16:15:55-03:00         3       0       0       0    3653   
3      2022-03-08T16:17:31-03:00         4   12040   -4004    8808    3126   
4      2022-03-08T16:17:48-03:00         5   11168   -3752    9536    3215   
...                          ...       ...     ...     ...     ...     ...   
13386  2022-10-04T11:57:38-03:00     13387      -1      -1      -1    3653   
13387  2022-10-04T12:07:38-03:00     13388      -1      -1      -1    3653   
13388  2022-10-04T12:37:38-03:00     13389      -1      -1      -1    3653   
13389  2022-10-04T12:57:33-03:00     13390      -1      -1      -1    3653   
13390  2022-10-04T13:07:32-03:00     13391      -1      -1      -1    3653   

       field5  field6  field7  
0         639     640     633  
1         639     640     630  
2         640     641     636  
3         645     642     637  
4         647     644     638  
...       ...     ...     ...  
13386     416     402     408  
13387     419     400     408  
13388     416     401     406  
13389     419     402     413  
13390     408     399     411  

[13391 rows x 9 columns]

In [ ]:
#Calcula o tempo
dados['tempo']=pd.to_datetime(dados['created_at'])

#Modifica os nomes das columnas
dados=dados.rename(columns={"field1":"acelX"})
dados=dados.rename(columns={"field2":"acelY"})
dados=dados.rename(columns={"field3":"acelZ"})
dados=dados.rename(columns={"field4":"temperatura"})
dados=dados.rename(columns={"field5":"U1"})
dados=dados.rename(columns={"field6":"U2"})
dados=dados.rename(columns={"field7":"U3"})
dados['ntemperatura']=dados['temperatura']/100
dados['AceleraçãoX']=dados['acelX']*9.81/16384
dados['AceleraçãoY']=dados['acelY']*9.81/16384
dados['AceleraçãoZ']=dados['acelZ']*9.81/16384
display(dados.head()) #Mostra as primeiras linhas do dataframe contendo os dados
display(dados.columns)

created_at  entry_id  acelX  acelY  acelZ  temperatura   U1  \
0  2022-03-08T16:15:17-03:00         1      0      0      0         3653  639   
1  2022-03-08T16:15:37-03:00         2     -1     -1     -1         3653  639   
2  2022-03-08T16:15:55-03:00         3      0      0      0         3653  640   
3  2022-03-08T16:17:31-03:00         4  12040  -4004   8808         3126  645   
4  2022-03-08T16:17:48-03:00         5  11168  -3752   9536         3215  647   

    U2   U3                     tempo  ntemperatura  AceleraçãoX  AceleraçãoY  \
0  640  633 2022-03-08 16:15:17-03:00         36.53     0.000000     0.000000   
1  640  630 2022-03-08 16:15:37-03:00         36.53    -0.000599    -0.000599   
2  641  636 2022-03-08 16:15:55-03:00         36.53     0.000000     0.000000   
3  642  637 2022-03-08 16:17:31-03:00         31.26     7.209009    -2.397415   
4  644  638 2022-03-08 16:17:48-03:00         32.15     6.686895    -2.246528   

   AceleraçãoZ  
0     0.000000  
1    -0.000599  
2     0.000000  
3     5.273833  
4     5.709727

Index(['created_at', 'entry_id', 'acelX', 'acelY', 'acelZ', 'temperatura',
       'U1', 'U2', 'U3', 'tempo', 'ntemperatura', 'AceleraçãoX', 'AceleraçãoY',
       'AceleraçãoZ'],
      dtype='object')

# Calculo dos angulos e das medias móveis

In [ ]:
#Calcula os ángulos nos eixos Y, X e Z  ,ainda que de forma lenta
dados["anX"]=np.degrees(np.arctan2(dados['acelY'],dados["acelZ"]))
dados["anY"]=np.degrees(np.arctan2(dados['acelX'],dados["acelZ"]))
dados["anZ"]=np.degrees(np.arctan2(dados['acelX'],dados["acelY"]))

#Ajusta os angulos para que todos sejam positivos...isso evita confusões visuais onde 180º  fica longe de -180º 
dados.loc[dados['anX'] < 0,'anX'] = (dados.loc[dados['anX'] < 0,'anX']) + 360
dados.loc[dados['anY'] < 0,'anY'] = (dados.loc[dados['anY'] < 0,'anY']) + 360
dados.loc[dados['anZ'] < 0,'anZ'] = (dados.loc[dados['anZ'] < 0,'anZ']) + 360
#for i in dados.index:         #varredura do atributo index (linhas) do dataframe
#    if dados.loc[i,'anX'] < 0:
#        dados.loc[i,'anX'] += 360 # equivalente a dados.loc[i,'anX'] = dados.loc[i,'anX'] + 360
#        
#    if dados.loc[i,'anY'] < 0:
#        dados.loc[i,'anY'] += 360
#        
#    if dados.loc[i,'anZ'] < 0:
#        dados.loc[i,'anZ']+= 360

#Limpeza de dados

dados['MedianX'] = dados['anX'].rolling(window=1000).mean()
dados['MedianY'] = dados['anY'].rolling(window=1000).mean()
dados['MedianZ'] = dados['anZ'].rolling(window=1000).mean()
dados['MDx'] = dados['MedianX'].diff()
dados['MDy'] = dados['MedianY'].diff()
dados['MDz'] = dados['MedianZ'].diff()

dados['axD'] = dados['anX'].diff()
dados['ayD'] = dados['anY'].diff()
dados['azD'] = dados['anZ'].diff()


C1= np.abs(dados['axD'])>50 
C2= np.abs(dados['MDx'])<5
dados = dados.drop(dados[ C1 & C2 ].index)

C1= np.abs(dados['ayD'])>50 
C2= np.abs(dados['MDy'])<5
dados = dados.drop(dados[ C1 & C2 ].index)

C1= np.abs(dados['azD'])>50 
C2= np.abs(dados['MDz'])<5
dados = dados.drop(dados[ C1 & C2 ].index)


In [ ]:
dados['MedianX']=dados['anX'].rolling(window=1000).mean()
dados['MedianY']=dados['anY'].rolling(window=1000).mean()
dados['MedianZ']=dados['anZ'].rolling(window=1000).mean()
display(dados)
print(dados.describe())

created_at  entry_id  acelX  acelY  acelZ  temperatura  \
0      2022-03-08T16:15:17-03:00         1      0      0      0         3653   
1      2022-03-08T16:15:37-03:00         2     -1     -1     -1         3653   
2      2022-03-08T16:15:55-03:00         3      0      0      0         3653   
3      2022-03-08T16:17:31-03:00         4  12040  -4004   8808         3126   
4      2022-03-08T16:17:48-03:00         5  11168  -3752   9536         3215   
...                          ...       ...    ...    ...    ...          ...   
13386  2022-10-04T11:57:38-03:00     13387     -1     -1     -1         3653   
13387  2022-10-04T12:07:38-03:00     13388     -1     -1     -1         3653   
13388  2022-10-04T12:37:38-03:00     13389     -1     -1     -1         3653   
13389  2022-10-04T12:57:33-03:00     13390     -1     -1     -1         3653   
13390  2022-10-04T13:07:32-03:00     13391     -1     -1     -1         3653   

        U1   U2   U3                     tempo  ...         anZ  MedianX  \
0      639  640  633 2022-03-08 16:15:17-03:00  ...    0.000000      NaN   
1      639  640  630 2022-03-08 16:15:37-03:00  ...  225.000000      NaN   
2      640  641  636 2022-03-08 16:15:55-03:00  ...    0.000000      NaN   
3      645  642  637 2022-03-08 16:17:31-03:00  ...  108.394966      NaN   
4      647  644  638 2022-03-08 16:17:48-03:00  ...  108.570283      NaN   
...    ...  ...  ...                       ...  ...         ...      ...   
13386  416  402  408 2022-10-04 11:57:38-03:00  ...  225.000000    225.0   
13387  419  400  408 2022-10-04 12:07:38-03:00  ...  225.000000    225.0   
13388  416  401  406 2022-10-04 12:37:38-03:00  ...  225.000000    225.0   
13389  419  402  413 2022-10-04 12:57:33-03:00  ...  225.000000    225.0   
13390  408  399  411 2022-10-04 13:07:32-03:00  ...  225.000000    225.0   

       MedianY  MedianZ  MDx  MDy  MDz         axD         ayD         azD  
0          NaN      NaN  NaN  NaN  NaN         NaN         NaN         NaN  
1          NaN      NaN  NaN  NaN  NaN  225.000000  225.000000  225.000000  
2          NaN      NaN  NaN  NaN  NaN -225.000000 -225.000000 -225.000000  
3          NaN      NaN  NaN  NaN  NaN  335.554085   53.812236  108.394966  
4          NaN      NaN  NaN  NaN  NaN    2.968442   -4.305195    0.175318  
...        ...      ...  ...  ...  ...         ...         ...         ...  
13386    225.0    225.0  0.0  0.0  0.0    0.000000    0.000000    0.000000  
13387    225.0    225.0  0.0  0.0  0.0    0.000000    0.000000    0.000000  
13388    225.0    225.0  0.0  0.0  0.0    0.000000    0.000000    0.000000  
13389    225.0    225.0  0.0  0.0  0.0    0.000000    0.000000    0.000000  
13390    225.0    225.0  0.0  0.0  0.0    0.000000    0.000000    0.000000  

[13206 rows x 26 columns]

           entry_id         acelX         acelY         acelZ   temperatura  \
count  13206.000000  13206.000000  13206.000000  13206.000000  13206.000000   
mean    6696.766697  -1034.052325  -1584.486521   3902.191201   3403.511586   
std     3869.465574   4278.675388   2354.595203   5996.925791    393.705656   
min        1.000000 -15752.000000  -5968.000000  -5564.000000  -3136.000000   
25%     3342.250000  -4988.000000  -4792.000000     -1.000000   3093.000000   
50%     6706.500000     -1.000000     -1.000000     -1.000000   3653.000000   
75%    10043.750000     -1.000000     -1.000000  12424.000000   3653.000000   
max    13391.000000  16776.000000  15104.000000  13540.000000  13068.000000   

                 U1            U2            U3  ntemperatura   AceleraçãoX  \
count  13206.000000  13206.000000  13206.000000  13206.000000  13206.000000   
mean     476.828638    425.373618    446.023777     34.035116     -0.619144   
std      179.939584     95.077678     77.735957    

In [ ]:
start_date = pd.to_datetime('2022-06-20 15:00:00 -03')  #definir a data desejada

m3 = (dados['tempo']<start_date)

teste_dados = dados[m3]

fig2=px.line(teste_dados,x='tempo',y=['MedianX','MedianY','MedianZ'],title="Médias Móveis",template="plotly_white",markers=True,hover_name='temperatura')
fig2['data'][0]['line']['color']='rgb(148,0,211)'
fig2['data'][1]['line']['color']='rgb(255,140,0)'
fig2['data'][2]['line']['color']='rgb(3,187,133)'

#Códigos para melhorar o grafico
fig2.update_traces(line=dict(width=4)) #Define aqui a largura das linhas do grafico neste caso com largura 
fig2.update_layout(font_family="Courier New",font_size = 16) #Define aqui o tipo de Fonte e o tamanho
fig2.update_traces(patch={"line": { "dash": 'dot'}}, selector={"legendgroup": "limite"})  #Define aqui o tipo de linha para a linha do limite
fig2.update_layout(legend_title=dict(text = '')) #Coloca um texto explicando as legendas.. neste caso deixei sem
fig2.update_layout(xaxis_title='Tempo',  yaxis_title='Leitura Sensor (Graus)') #titulos dos eixos X e Y

#Configuração para deixar a opção de baixar a imagem com maior resolução.
config = {
  'toImageButtonOptions': {
    'format': 'jpeg', # one of png, svg, jpeg, webp
    'filename': 'custom_image',

    'scale':3 # Multiply title/legend/axis/canvas sizes by this factor
  }
}

fig2.show(config=config)

### **TEMPERATURA COM DADOS COMPLETOS**

In [ ]:
start_date = pd.to_datetime('2022-06-20 15:00:00 -03')  #definir a data desejada

m3 = (dados['tempo']<start_date)

teste_dados = dados[m3]

fig2=px.line(teste_dados,x='tempo',y=['ntemperatura'],title="Temperatura",template="plotly_white",markers=True,hover_name='temperatura')
fig2['data'][0]['line']['color']='rgb(255,0,0)'

#Códigos para melhorar o grafico
fig2.update_traces(line=dict(width=4)) #Define aqui a largura das linhas do grafico neste caso com largura 
fig2.update_layout(font_family="Courier New",font_size = 16) #Define aqui o tipo de Fonte e o tamanho
fig2.update_traces(patch={"line": { "dash": 'dot'}}, selector={"legendgroup": "limite"})  #Define aqui o tipo de linha para a linha do limite
fig2.update_layout(legend_title=dict(text = '')) #Coloca um texto explicando as legendas.. neste caso deixei sem
fig2.update_layout(xaxis_title='Tempo',  yaxis_title='Leitura Sensor (ºC)') #titulos dos eixos X e Y

#Configuração para deixar a opção de baixar a imagem com maior resolução.
config = {
  'toImageButtonOptions': {
    'format': 'jpeg', # one of png, svg, jpeg, webp
    'filename': 'custom_image',

    'scale':3 # Multiply title/legend/axis/canvas sizes by this factor
  }
}

fig2.show(config=config)

### **GRÁFICO DE ACELERAÇÃO**

In [ ]:
start_date = pd.to_datetime('2022-06-20 15:00:00 -03')  #definir a data desejada


m1 = (dados['tempo']<start_date)

teste_dados = dados[m1]
#Forma de plotar em ploty
fig2=px.line(teste_dados,x='tempo',y=['acelX','acelY','acelZ'],title="Acelerações (bits)",template="plotly_white",markers=True,hover_name='ntemperatura')
fig2['data'][0]['line']['color']='rgb(148,0,211)'
fig2['data'][1]['line']['color']='rgb(255,140,0)'
fig2['data'][2]['line']['color']='rgb(3,187,133)'

#Códigos para melhorar o grafico
fig2.update_traces(line=dict(width=4)) #Define aqui a largura das linhas do grafico neste caso com largura 
fig2.update_layout(font_family="Courier New",font_size = 16) #Define aqui o tipo de Fonte e o tamanho
fig2.update_traces(patch={"line": { "dash": 'dot'}}, selector={"legendgroup": "limite"})  #Define aqui o tipo de linha para a linha do limite
fig2.update_layout(legend_title=dict(text = '')) #Coloca um texto explicando as legendas.. neste caso deixei sem
fig2.update_layout(xaxis_title='Tempo',  yaxis_title='Leitura Sensor (bits)') #titulos dos eixos X e Y

#Configuração para deixar a opção de baixar a imagem com maior resolução.
config = {
  'toImageButtonOptions': {
    'format': 'jpeg', # one of png, svg, jpeg, webp
    'filename': 'custom_image',

    'scale':3 # Multiply title/legend/axis/canvas sizes by this factor
  }
}

fig2.show(config=config)

In [ ]:
start_date = pd.to_datetime('2022-06-20 15:00:00 -03')  #definir a data desejada


m1 = (dados['tempo']<start_date)

teste_dados = dados[m1]
#Forma de plotar em ploty
fig2=px.line(teste_dados,x='tempo',y=['anX','anY','anZ'],title="Ângulos",template="plotly_white",markers=True,hover_name='ntemperatura')
fig2['data'][0]['line']['color']='rgb(148,0,211)'
fig2['data'][1]['line']['color']='rgb(255,140,0)'
fig2['data'][2]['line']['color']='rgb(3,187,133)'

#Códigos para melhorar o grafico
fig2.update_traces(line=dict(width=4)) #Define aqui a largura das linhas do grafico neste caso com largura 
fig2.update_layout(font_family="Courier New",font_size = 16) #Define aqui o tipo de Fonte e o tamanho
fig2.update_traces(patch={"line": { "dash": 'dot'}}, selector={"legendgroup": "limite"})  #Define aqui o tipo de linha para a linha do limite
fig2.update_layout(legend_title=dict(text = '')) #Coloca um texto explicando as legendas.. neste caso deixei sem
fig2.update_layout(xaxis_title='Tempo',  yaxis_title='Leitura Sensor (Graus)') #titulos dos eixos X e Y

#Configuração para deixar a opção de baixar a imagem com maior resolução.
config = {
  'toImageButtonOptions': {
    'format': 'jpeg', # one of png, svg, jpeg, webp
    'filename': 'custom_image',

    'scale':3 # Multiply title/legend/axis/canvas sizes by this factor
  }
}

fig2.show(config=config)

In [ ]:
start_date = pd.to_datetime('2022-06-20 15:00:00 -03')  #definir a data desejada


m1 = (dados['tempo']<start_date)

teste_dados = dados[m1]
#Forma de plotar em ploty
fig2=px.line(teste_dados,x='tempo',y=['AceleraçãoX','AceleraçãoY','AceleraçãoZ'],title="Acelerações (m/s²)",template="plotly_white",markers=True,hover_name='ntemperatura')
fig2['data'][0]['line']['color']='rgb(148,0,211)'
fig2['data'][1]['line']['color']='rgb(255,140,0)'
fig2['data'][2]['line']['color']='rgb(3,187,133)'

#Códigos para melhorar o grafico
fig2.update_traces(line=dict(width=4)) #Define aqui a largura das linhas do grafico neste caso com largura 
fig2.update_layout(font_family="Courier New",font_size = 16) #Define aqui o tipo de Fonte e o tamanho
fig2.update_traces(patch={"line": { "dash": 'dot'}}, selector={"legendgroup": "limite"})  #Define aqui o tipo de linha para a linha do limite
fig2.update_layout(legend_title=dict(text = '')) #Coloca um texto explicando as legendas.. neste caso deixei sem
fig2.update_layout(xaxis_title='Tempo',  yaxis_title='Leitura Sensor (m/s²)') #titulos dos eixos X e Y

#Configuração para deixar a opção de baixar a imagem com maior resolução.
config = {
  'toImageButtonOptions': {
    'format': 'jpeg', # one of png, svg, jpeg, webp
    'filename': 'custom_image',

    'scale':3 # Multiply title/legend/axis/canvas sizes by this factor
  }
}

fig2.show(config=config)

### **UMIDADES**

In [ ]:
start_date = pd.to_datetime('2022-06-20 15:00:00 -03')  #definir a data desejada


m1 = (dados['tempo']<start_date)

teste_dados = dados[m1]
#Forma de plotar em ploty
fig2=px.line(teste_dados,x='tempo',y=['U1','U2','U3'],title="Umidades",template="plotly_white",markers=True,hover_name='ntemperatura')
fig2['data'][0]['line']['color']='rgb(135,206,250)'
fig2['data'][1]['line']['color']='rgb(0,191,255)'
fig2['data'][2]['line']['color']='rgb(25,25,112)'

#Códigos para melhorar o grafico
fig2.update_traces(line=dict(width=4)) #Define aqui a largura das linhas do grafico neste caso com largura 
fig2.update_layout(font_family="Courier New",font_size = 16) #Define aqui o tipo de Fonte e o tamanho
fig2.update_traces(patch={"line": { "dash": 'dot'}}, selector={"legendgroup": "limite"})  #Define aqui o tipo de linha para a linha do limite
fig2.update_layout(legend_title=dict(text = '')) #Coloca um texto explicando as legendas.. neste caso deixei sem
fig2.update_layout(xaxis_title='Tempo',  yaxis_title='Leitura Sensor (bits)') #titulos dos eixos X e Y

#Configuração para deixar a opção de baixar a imagem com maior resolução.
config = {
  'toImageButtonOptions': {
    'format': 'jpeg', # one of png, svg, jpeg, webp
    'filename': 'custom_image',

    'scale':3 # Multiply title/legend/axis/canvas sizes by this factor
  }
}

fig2.show(config=config)

### **GRÁFICOS COM TODOS OS DADOS**

In [ ]:
start_date = pd.to_datetime('2022-06-20 15:00:00 -03')  #definir a data desejada


m1 = (dados['tempo']<start_date)

teste_dados = dados[m1]
#Forma de plotar em ploty

fig2=px.line(teste_dados,x='tempo',y=['acelX','acelY','acelZ','ntemperatura','U1','U2','U3'],title="Teste em Campo - Estufa UFF",template="plotly_white",markers=True,hover_name='temperatura')
fig2['data'][0]['line']['color']='rgb(148,0,211)'
fig2['data'][1]['line']['color']='rgb(255,140,0)'
fig2['data'][2]['line']['color']='rgb(3,187,133)'
fig2['data'][3]['line']['color']='rgb(255,0,0)'
fig2['data'][4]['line']['color']='rgb(135,206,250)'
fig2['data'][5]['line']['color']='rgb(0,191,255)'
fig2['data'][6]['line']['color']='rgb(25,25,112)'

#Códigos para melhorar o grafico
fig2.update_traces(line=dict(width=4)) #Define aqui a largura das linhas do grafico neste caso com largura 
fig2.update_layout(font_family="Courier New",font_size = 16) #Define aqui o tipo de Fonte e o tamanho
fig2.update_traces(patch={"line": { "dash": 'dot'}}, selector={"legendgroup": "limite"})  #Define aqui o tipo de linha para a linha do limite
fig2.update_layout(legend_title=dict(text = '')) #Coloca um texto explicando as legendas.. neste caso deixei sem
fig2.update_layout(xaxis_title='Tempo',  yaxis_title='Leitura Sensor (bits)') #titulos dos eixos X e Y

#Configuração para deixar a opção de baixar a imagem com maior resolução.
config = {
  'toImageButtonOptions': {
    'format': 'jpeg', # one of png, svg, jpeg, webp
    'filename': 'custom_image',

    'scale':3 # Multiply title/legend/axis/canvas sizes by this factor
  }
}

fig2.show(config=config)

### **REDUZINDO O TAMANHO DOS DADOS**

In [ ]:
intervalo = 100  #De quantos em quantos dados serão utilizados do dataframe antigo
nindex = range(0,len(dados),intervalo)
dados_reduzido = dados.iloc[nindex,:]
print(dados_reduzido)

                      created_at  entry_id  acelX  acelY  acelZ  temperatura  \
0      2022-03-08T16:15:17-03:00         1      0      0      0         3653   
100    2022-03-09T12:19:14-03:00       101   6572    236  -3084         2811   
200    2022-03-09T12:58:53-03:00       201  16492    228  -3048         2811   
300    2022-03-09T13:36:01-03:00       301  16548   -536  -1536         2820   
400    2022-03-09T14:09:54-03:00       401  16584   -932  -1320         2669   
...                          ...       ...    ...    ...    ...          ...   
12981  2022-09-29T09:08:57-03:00     12982     -1     -1     -1         3653   
13081  2022-09-30T18:15:52-03:00     13082     -1     -1     -1         3653   
13181  2022-10-02T04:42:43-03:00     13182     -1     -1     -1         3653   
13283  2022-10-03T09:50:02-03:00     13284     -1     -1     -1         3653   
13385  2022-10-04T11:17:42-03:00     13386     -1     -1     -1         3653   

        U1   U2   U3                   

### **TEMPERATURA COM DADOS REDUZIDOS**

In [ ]:
start_date = pd.to_datetime('2022-06-20 15:00:00 -03')  #definir a data desejada

m3 = (dados_reduzido['tempo']<start_date)

teste_dados = dados_reduzido[m3]

fig2=px.line(teste_dados,x='tempo',y=['ntemperatura'],title="Temperatura",template="plotly_white",markers=True,hover_name='temperatura')
fig2['data'][0]['line']['color']='rgb(255,0,0)'

#Códigos para melhorar o grafico
fig2.update_traces(line=dict(width=4)) #Define aqui a largura das linhas do grafico neste caso com largura 
fig2.update_layout(font_family="Courier New",font_size = 16) #Define aqui o tipo de Fonte e o tamanho
fig2.update_traces(patch={"line": { "dash": 'dot'}}, selector={"legendgroup": "limite"})  #Define aqui o tipo de linha para a linha do limite
fig2.update_layout(legend_title=dict(text = '')) #Coloca um texto explicando as legendas.. neste caso deixei sem
fig2.update_layout(xaxis_title='Tempo',  yaxis_title='Leitura Sensor (ºC)') #titulos dos eixos X e Y

#Configuração para deixar a opção de baixar a imagem com maior resolução.
config = {
  'toImageButtonOptions': {
    'format': 'jpeg', # one of png, svg, jpeg, webp
    'filename': 'custom_image',

    'scale':3 # Multiply title/legend/axis/canvas sizes by this factor
  }
}

fig2.show(config=config)

### **GRÁFICOS DE ACELERAÇÃO COM DADOS REDUZIDOS**

In [ ]:
start_date = pd.to_datetime('2022-06-20 15:00:00 -03')  #definir a data desejada


m1 = (dados_reduzido['tempo']<start_date)

teste_dados = dados_reduzido[m1]
#Forma de plotar em ploty
fig2=px.line(teste_dados,x='tempo',y=['anX','anY','anZ'],title="Ângulos",template="plotly_white",markers=True,hover_name='ntemperatura')
fig2['data'][0]['line']['color']='rgb(148,0,211)'
fig2['data'][1]['line']['color']='rgb(255,140,0)'
fig2['data'][2]['line']['color']='rgb(3,187,133)'

#Códigos para melhorar o grafico
fig2.update_traces(line=dict(width=4)) #Define aqui a largura das linhas do grafico neste caso com largura 
fig2.update_layout(font_family="Courier New",font_size = 16) #Define aqui o tipo de Fonte e o tamanho
fig2.update_traces(patch={"line": { "dash": 'dot'}}, selector={"legendgroup": "limite"})  #Define aqui o tipo de linha para a linha do limite
fig2.update_layout(legend_title=dict(text = '')) #Coloca um texto explicando as legendas.. neste caso deixei sem
fig2.update_layout(xaxis_title='Tempo',  yaxis_title='Leitura Sensor (Graus)') #titulos dos eixos X e Y

#Configuração para deixar a opção de baixar a imagem com maior resolução.
config = {
  'toImageButtonOptions': {
    'format': 'jpeg', # one of png, svg, jpeg, webp
    'filename': 'custom_image',

    'scale':3 # Multiply title/legend/axis/canvas sizes by this factor
  }
}

fig2.show(config=config)

In [ ]:
start_date = pd.to_datetime('2022-06-20 15:00:00 -03')  #definir a data desejada


m1 = (dados_reduzido['tempo']<start_date)

teste_dados = dados_reduzido[m1]
#Forma de plotar em ploty
fig2=px.line(teste_dados,x='tempo',y=['AceleraçãoX','AceleraçãoY','AceleraçãoZ'],title="Acelerações (m/s²)",template="plotly_white",markers=True,hover_name='ntemperatura')
fig2['data'][0]['line']['color']='rgb(148,0,211)'
fig2['data'][1]['line']['color']='rgb(255,140,0)'
fig2['data'][2]['line']['color']='rgb(3,187,133)'

#Códigos para melhorar o grafico
fig2.update_traces(line=dict(width=4)) #Define aqui a largura das linhas do grafico neste caso com largura 
fig2.update_layout(font_family="Courier New",font_size = 16) #Define aqui o tipo de Fonte e o tamanho
fig2.update_traces(patch={"line": { "dash": 'dot'}}, selector={"legendgroup": "limite"})  #Define aqui o tipo de linha para a linha do limite
fig2.update_layout(legend_title=dict(text = '')) #Coloca um texto explicando as legendas.. neste caso deixei sem
fig2.update_layout(xaxis_title='Tempo',  yaxis_title='Leitura Sensor (m/s²)') #titulos dos eixos X e Y

#Configuração para deixar a opção de baixar a imagem com maior resolução.
config = {
  'toImageButtonOptions': {
    'format': 'jpeg', # one of png, svg, jpeg, webp
    'filename': 'custom_image',

    'scale':3 # Multiply title/legend/axis/canvas sizes by this factor
  }
}

fig2.show(config=config)

### **UMIDADE REDUZIDA**

In [ ]:
start_date = pd.to_datetime('2022-06-20 15:00:00 -03')  #definir a data desejada


m1 = (dados_reduzido['tempo']<start_date)

teste_dados = dados_reduzido[m1]
#Forma de plotar em ploty
fig2=px.line(teste_dados,x='tempo',y=['U1','U2','U3'],title="Umidades (com temperatura)",template="plotly_white",markers=True,hover_name='ntemperatura')
fig2['data'][0]['line']['color']='rgb(135,206,250)'
fig2['data'][1]['line']['color']='rgb(0,191,255)'
fig2['data'][2]['line']['color']='rgb(25,25,112)'

#Códigos para melhorar o grafico
fig2.update_traces(line=dict(width=4)) #Define aqui a largura das linhas do grafico neste caso com largura 
fig2.update_layout(font_family="Courier New",font_size = 16) #Define aqui o tipo de Fonte e o tamanho
fig2.update_traces(patch={"line": { "dash": 'dot'}}, selector={"legendgroup": "limite"})  #Define aqui o tipo de linha para a linha do limite
fig2.update_layout(legend_title=dict(text = '')) #Coloca um texto explicando as legendas.. neste caso deixei sem
fig2.update_layout(xaxis_title='Tempo',  yaxis_title='Leitura Sensor (bits)') #titulos dos eixos X e Y

#Configuração para deixar a opção de baixar a imagem com maior resolução.
config = {
  'toImageButtonOptions': {
    'format': 'jpeg', # one of png, svg, jpeg, webp
    'filename': 'custom_image',

    'scale':3 # Multiply title/legend/axis/canvas sizes by this factor
  }
}

fig2.show(config=config)

### **DADOS TOTAIS REDUZIDOS**

In [ ]:
start_date = pd.to_datetime('2022-06-20 15:00:00 -03')  #definir a data desejada


m1 = (dados_reduzido['tempo']<start_date)

teste_dados = dados_reduzido[m1]
#Forma de plotar em ploty

fig2=px.line(teste_dados,x='tempo',y=['anX','anY','anZ','ntemperatura','U1','U2','U3'],title="Teste em Campo - Estufa UFF",template="plotly_white",markers=True,hover_name='temperatura')
fig2['data'][0]['line']['color']='rgb(148,0,211)'
fig2['data'][1]['line']['color']='rgb(255,140,0)'
fig2['data'][2]['line']['color']='rgb(3,187,133)'
fig2['data'][3]['line']['color']='rgb(255,0,0)'
fig2['data'][4]['line']['color']='rgb(135,206,250)'
fig2['data'][5]['line']['color']='rgb(0,191,255)'
fig2['data'][6]['line']['color']='rgb(25,25,112)'

#Códigos para melhorar o grafico
fig2.update_traces(line=dict(width=4)) #Define aqui a largura das linhas do grafico neste caso com largura 
fig2.update_layout(font_family="Courier New",font_size = 16) #Define aqui o tipo de Fonte e o tamanho
fig2.update_traces(patch={"line": { "dash": 'dot'}}, selector={"legendgroup": "limite"})  #Define aqui o tipo de linha para a linha do limite
fig2.update_layout(legend_title=dict(text = '')) #Coloca um texto explicando as legendas.. neste caso deixei sem
fig2.update_layout(xaxis_title='Tempo',  yaxis_title='Leitura Sensor (graus; ºC; bits)') #titulos dos eixos X e Y

#Configuração para deixar a opção de baixar a imagem com maior resolução.
config = {
  'toImageButtonOptions': {
    'format': 'jpeg', # one of png, svg, jpeg, webp
    'filename': 'custom_image',

    'scale':3 # Multiply title/legend/axis/canvas sizes by this factor
  }
}

fig2.show(config=config)

### **ANÁLISE DOS DADOS**

In [ ]:
start_date = pd.to_datetime('2021-08-29 15:00:00 -03')  #definir a data desejada
end_date = pd.to_datetime('2021-09-15 15:00:00 -03')  #definir a data desejada

m1 = (dados['tempo']>start_date)
m2 = (dados['tempo']<end_date)
teste_dados = dados[m2]


print("Dados antes da borracha")
display(teste_dados.describe())

start_date = pd.to_datetime('2021-09-17 15:00:00 -03')  #definir a data desejada
end_date = pd.to_datetime('2021-09-22 15:00:00 -03')  #definir a data desejada


m1 = (dados['tempo']>start_date)
m2 = (dados['tempo']<end_date)
teste_dados = dados[m1&m2]
print("Dados depois da borracha")
display(teste_dados.describe())

start_date = pd.to_datetime('2021-09-28 15:00:00 -03')  #definir a data desejada
end_date = pd.to_datetime('2022-11-10 23:00:00 -03')  #definir a data desejada

m1 = (dados['tempo']>start_date)
m2 = (dados['tempo']<end_date)
teste_dados = dados[m2]

print("Dados teste controlado na universidade - departamento")
display(teste_dados.describe())

start_date = pd.to_datetime('2022-04-10 00:00:00 -03')  #definir a data desejada
end_date = pd.to_datetime('2022-05-22 23:00:00 -03')  #definir a data desejada

m1 = (dados['tempo']>start_date)
m2 = (dados['tempo']<end_date)
teste_dados = dados[m2]

print("Dados teste em campo - Estufa")
display(teste_dados.describe())

Dados antes da borracha


entry_id  acelX  acelY  acelZ  temperatura   U1   U2   U3  \
count       0.0    0.0    0.0    0.0          0.0  0.0  0.0  0.0   
mean        NaN    NaN    NaN    NaN          NaN  NaN  NaN  NaN   
std         NaN    NaN    NaN    NaN          NaN  NaN  NaN  NaN   
min         NaN    NaN    NaN    NaN          NaN  NaN  NaN  NaN   
25%         NaN    NaN    NaN    NaN          NaN  NaN  NaN  NaN   
50%         NaN    NaN    NaN    NaN          NaN  NaN  NaN  NaN   
75%         NaN    NaN    NaN    NaN          NaN  NaN  NaN  NaN   
max         NaN    NaN    NaN    NaN          NaN  NaN  NaN  NaN   

       ntemperatura  AceleraçãoX  ...  anZ  MedianX  MedianY  MedianZ  MDx  \
count           0.0          0.0  ...  0.0      0.0      0.0      0.0  0.0   
mean            NaN          NaN  ...  NaN      NaN      NaN      NaN  NaN   
std             NaN          NaN  ...  NaN      NaN      NaN      NaN  NaN   
min             NaN          NaN  ...  NaN      NaN      NaN      NaN  NaN   
25%             NaN          NaN  ...  NaN      NaN      NaN      NaN  NaN   
50%             NaN          NaN  ...  NaN      NaN      NaN      NaN  NaN   
75%             NaN          NaN  ...  NaN      NaN      NaN      NaN  NaN   
max             NaN          NaN  ...  NaN      NaN      NaN      NaN  NaN   

       MDy  MDz  axD  ayD  azD  
count  0.0  0.0  0.0  0.0  0.0  
mean   NaN  NaN  NaN  NaN  NaN  
std    NaN  NaN  NaN  NaN  NaN  
min    NaN  NaN  NaN  NaN  NaN  
25%    NaN  NaN  NaN  NaN  NaN  
50%    NaN  NaN  NaN  NaN  NaN  
75%    NaN  NaN  NaN  NaN  NaN  
max    NaN  NaN  NaN  NaN  NaN  

[8 rows x 24 columns]

Dados depois da borracha


entry_id  acelX  acelY  acelZ  temperatura   U1   U2   U3  \
count       0.0    0.0    0.0    0.0          0.0  0.0  0.0  0.0   
mean        NaN    NaN    NaN    NaN          NaN  NaN  NaN  NaN   
std         NaN    NaN    NaN    NaN          NaN  NaN  NaN  NaN   
min         NaN    NaN    NaN    NaN          NaN  NaN  NaN  NaN   
25%         NaN    NaN    NaN    NaN          NaN  NaN  NaN  NaN   
50%         NaN    NaN    NaN    NaN          NaN  NaN  NaN  NaN   
75%         NaN    NaN    NaN    NaN          NaN  NaN  NaN  NaN   
max         NaN    NaN    NaN    NaN          NaN  NaN  NaN  NaN   

       ntemperatura  AceleraçãoX  ...  anZ  MedianX  MedianY  MedianZ  MDx  \
count           0.0          0.0  ...  0.0      0.0      0.0      0.0  0.0   
mean            NaN          NaN  ...  NaN      NaN      NaN      NaN  NaN   
std             NaN          NaN  ...  NaN      NaN      NaN      NaN  NaN   
min             NaN          NaN  ...  NaN      NaN      NaN      NaN  NaN   
25%             NaN          NaN  ...  NaN      NaN      NaN      NaN  NaN   
50%             NaN          NaN  ...  NaN      NaN      NaN      NaN  NaN   
75%             NaN          NaN  ...  NaN      NaN      NaN      NaN  NaN   
max             NaN          NaN  ...  NaN      NaN      NaN      NaN  NaN   

       MDy  MDz  axD  ayD  azD  
count  0.0  0.0  0.0  0.0  0.0  
mean   NaN  NaN  NaN  NaN  NaN  
std    NaN  NaN  NaN  NaN  NaN  
min    NaN  NaN  NaN  NaN  NaN  
25%    NaN  NaN  NaN  NaN  NaN  
50%    NaN  NaN  NaN  NaN  NaN  
75%    NaN  NaN  NaN  NaN  NaN  
max    NaN  NaN  NaN  NaN  NaN  

[8 rows x 24 columns]

Dados teste controlado na universidade - departamento


entry_id         acelX         acelY         acelZ   temperatura  \
count  13206.000000  13206.000000  13206.000000  13206.000000  13206.000000   
mean    6696.766697  -1034.052325  -1584.486521   3902.191201   3403.511586   
std     3869.465574   4278.675388   2354.595203   5996.925791    393.705656   
min        1.000000 -15752.000000  -5968.000000  -5564.000000  -3136.000000   
25%     3342.250000  -4988.000000  -4792.000000     -1.000000   3093.000000   
50%     6706.500000     -1.000000     -1.000000     -1.000000   3653.000000   
75%    10043.750000     -1.000000     -1.000000  12424.000000   3653.000000   
max    13391.000000  16776.000000  15104.000000  13540.000000  13068.000000   

                 U1            U2            U3  ntemperatura   AceleraçãoX  \
count  13206.000000  13206.000000  13206.000000  13206.000000  13206.000000   
mean     476.828638    425.373618    446.023777     34.035116     -0.619144   
std      179.939584     95.077678     77.735957      3.937057      2.561878   
min      247.000000   -956.000000  -1340.000000    -31.360000     -9.431587   
25%      389.000000    355.000000    383.000000     30.930000     -2.986589   
50%      475.000000    393.000000    426.000000     36.530000     -0.000599   
75%      547.000000    467.000000    500.000000     36.530000     -0.000599   
max    16552.000000    890.000000    875.000000    130.680000     10.044712   

       ...           anZ       MedianX       MedianY       MedianZ  \
count  ...  13206.000000  12207.000000  12207.000000  12207.000000   
mean   ...    220.058570    262.218541    260.965478    223.667973   
std    ...     26.230646     50.687521     50.283894      7.149497   
min    ...      0.000000    224.910000    213.139801    160.894216   
25%    ...    225.000000    225.000000    225.000000    224.775000   
50%    ...    225.000000    225.000000    225.000000    225.000000   
75%    ...    225.000000    337.512041    337.908955    225.000000   
max    ...    270.395767    339.182035    338.944157    228.190587   

                MDx           MDy           MDz           axD           ayD  \
count  12206.000000  12206.000000  12206.000000  13205.000000  13205.000000   
mean      -0.002619      0.001811      0.006354      0.025669      0.025896   
std        0.045001      0.059565      0.031292      8.729272      7.458282   
min       -0.113698     -0.114594     -0.225000   -338.238843   -318.402061   
25%       -0.000342      0.000000      0.000000      0.000000      0.000000   
50%        0.000000      0.000000      0.000000      0.000000      0.000000   
75%        0.000000      0.000000      0.000000      0.000000      0.000000   
max        0.339675      0.338818      0.226861    353.004332    318.913990   

                azD  
count  13205.000000  
mean       0.016720  
std        7.428826  
min     -265.708965  
25%        0.000000  
50%        0.000000  
75%        0.000000  
max      265.866788  

[8 rows x 24 columns]

Dados teste em campo - Estufa


entry_id         acelX         acelY         acelZ   temperatura  \
count  4638.000000   4638.000000   4638.000000   4638.000000   4638.000000   
mean   2346.397370  -2916.750108  -4480.805951  11048.529107   2949.497628   
std    1360.001005   6821.761843   1639.352818   4780.388041    336.600153   
min       1.000000 -15752.000000  -5952.000000  -5564.000000  -3136.000000   
25%    1166.250000  -5092.000000  -5248.000000  12348.000000   2754.000000   
50%    2351.500000  -5038.000000  -4940.000000  12812.000000   2952.000000   
75%    3524.750000  -4972.000000  -4776.000000  13100.000000   3112.000000   
max    4702.000000  16776.000000  15104.000000  13540.000000  13068.000000   

                 U1           U2           U3  ntemperatura  AceleraçãoX  ...  \
count   4638.000000  4638.000000  4638.000000   4638.000000  4638.000000  ...   
mean     444.382061   513.429280   458.733506     29.494976    -1.746418  ...   
std      271.127534   106.018948    95.277551      3.366002     4.084563  ...   
min      247.000000  -956.000000 -1340.000000    -31.360000    -9.431587  ...   
25%      354.000000   459.000000   382.000000     27.540000    -3.048860  ...   
50%      444.000000   484.000000   428.000000     29.520000    -3.016527  ...   
75%      489.750000   618.000000   517.000000     31.120000    -2.977009  ...   
max    16552.000000   890.000000   875.000000    130.680000    10.044712  ...   

               anZ      MedianX      MedianY      MedianZ          MDx  \
count  4638.000000  3639.000000  3639.000000  3639.000000  3638.000000   
mean    210.995281   333.830183   329.361624   220.948996     0.020206   
std      42.682245    14.003593    25.849706    12.668170     0.053747   
min       0.000000   266.036093   213.139801   160.894216    -0.017611   
25%     223.541956   338.136678   337.933396   223.843744    -0.001122   
50%     224.954455   338.366889   338.134053   225.004988    -0.000454   
75%     226.045901   338.625718   338.723843   225.881134     0.000047   
max     270.395767   339.182035   338.944157   228.190587     0.339675   

               MDy          MDz          axD          ayD          azD  
count  3638.000000  3638.000000  4637.000000  4637.000000  4637.000000  
mean      0.035207     0.017933     0.073161     0.073772     0.047662  
std       0.084077     0.050044    14.731772    12.586763    12.537093  
min      -0.002981    -0.044290  -338.238843  -318.402061  -265.708965  
25%      -0.000495    -0.001570    -0.231681    -0.242872    -0.384590  
50%       0.000334    -0.000937     0.004716    -0.002592    -0.001137  
75%       0.001034    -0.000104     0.243889     0.240057     0.368287  
max       0.338818     0.226861   353.004332   318.913990   265.866788  

[8 rows x 24 columns]